In [1]:
import tensorflow as tf
import tensorflow_addons as tfa
import pandas as pd
from tqdm import tqdm
import numpy as np
from sklearn.preprocessing import StandardScaler, MinMaxScaler
from tensorflow.keras.callbacks import EarlyStopping, ReduceLROnPlateau
from kerastuner.tuners import RandomSearch
from kerastuner.engine.hyperparameters import HyperParameters
from datetime import datetime
import random
from tensorflow.keras import backend
import kerastuner
from sklearn.decomposition import PCA

In [2]:
tf.keras.backend.set_floatx('float64')
physical_devices = tf.config.list_physical_devices('GPU') 
tf.config.experimental.set_memory_growth(physical_devices[0], True)

In [3]:
dir_name = str(datetime.now())[:-10].replace(' ','-')
dir_name = dir_name.replace(':','')

In [4]:
directory = f'logs\\{dir_name}'

In [5]:
def engineer_features(train, test):
    
    features_g = list(train.filter(regex=("g-.*")).columns)
    features_c = list(train.filter(regex=("c-.*")).columns)
    
    for df in [train, test]:
        df['g_sum'] = df[features_g].sum(axis = 1)
        df['g_mean'] = df[features_g].mean(axis = 1)
        df['g_std'] = df[features_g].std(axis = 1)
        df['g_kurt'] = df[features_g].kurtosis(axis = 1)
        df['g_skew'] = df[features_g].skew(axis = 1)
        df['c_sum'] = df[features_c].sum(axis = 1)
        df['c_mean'] = df[features_c].mean(axis = 1)
        df['c_std'] = df[features_c].std(axis = 1)
        df['c_kurt'] = df[features_c].kurtosis(axis = 1)
        df['c_skew'] = df[features_c].skew(axis = 1)
        df['gc_sum'] = df[features_g + features_c].sum(axis = 1)
        df['gc_mean'] = df[features_g + features_c].mean(axis = 1)
        df['gc_std'] = df[features_g + features_c].std(axis = 1)
        df['gc_kurt'] = df[features_g + features_c].kurtosis(axis = 1)
        df['gc_skew'] = df[features_g + features_c].skew(axis = 1)
        
    return train, test

In [6]:
n_components_ge = 10
n_components_cv = 2
def make_train_test():
    train_raw = pd.read_csv('train_features.csv')
    labels = pd.read_csv('train_targets_scored.csv')

    #train_raw = pd.read_csv('/kaggle/input/lish-moa/train_features.csv')
    #labels = pd.read_csv('/kaggle/input/lish-moa/train_targets_scored.csv')

    #drop controls
    all_features = train_raw[train_raw['cp_type'] == 'trt_cp']

    #decode
    all_features['cp_time'] = all_features['cp_time'].map({ 24: 0, 48: 0.5, 72: 1})
    all_features['cp_dose'] = all_features['cp_dose'].map({'D1': 0, 'D2': 1})

    # drop controls from labels
    labels['cp_type'] = train_raw['cp_type']
    labels = labels[labels['cp_type'] == 'trt_cp']
    labels.drop('cp_type',axis=1,inplace=True)

    #train_test_split
    train_features = all_features.sample(int(len(all_features)*.9))
    test_features = all_features.drop(list(train_features.index),axis=0)
    train_labels = labels.loc[list(train_features.index)]
    test_labels = labels.drop(list(train_features.index),axis=0)

    train_features.reset_index(inplace=True,drop=True)
    test_features.reset_index(inplace=True,drop=True)
    train_labels.reset_index(inplace=True,drop=True)
    test_labels.reset_index(inplace=True,drop=True)

    '''print('Check train / test split is correct: \n')
    print('train sig_ids match:')
    print(list(train_features['sig_id']) == list(train_labels['sig_id']))
    print('test sig_ids match:')
    print(list(test_features['sig_id']) == list(test_labels['sig_id']))'''

    #get gene expression dataframe
    gene_exp_df = train_features.filter(regex=("g-.*"))
    gene_exp_df_test = test_features.filter(regex=("g-.*"))

    #get cell viability dataframe
    cell_via_df = train_features.filter(regex=("c-.*"))
    cell_via_df_test = test_features.filter(regex=("c-.*"))

    PCA_ge = PCA(n_components=n_components_ge)
    PCA_cv = PCA(n_components=n_components_cv)

    pca_gene_exp = PCA_ge.fit_transform(gene_exp_df)
    pca_cell_via = PCA_cv.fit_transform(cell_via_df)

    pca_gene_exp_test = PCA_ge.transform(gene_exp_df_test)
    pca_cell_via_test = PCA_cv.transform(cell_via_df_test)

    #ge-train
    cols = [f'pcge_{i}' for i in range(1,n_components_ge+1)]
    pca_gene_exp = pd.DataFrame(pca_gene_exp, columns=cols)
    pca_gene_exp['sig_id'] = train_features['sig_id']

    #ge-test
    cols = [f'pcge_{i}' for i in range(1,n_components_ge+1)]
    pca_gene_exp_test = pd.DataFrame(pca_gene_exp_test, columns=cols)
    pca_gene_exp_test['sig_id'] = test_features['sig_id']

    #cv-train
    cols = [f'pccv_{i}' for i in range(1,n_components_cv+1)]
    pca_cell_via = pd.DataFrame(pca_cell_via, columns=cols)
    pca_cell_via['sig_id'] = train_features['sig_id']

    #cv-test
    cols = [f'pccv_{i}' for i in range(1,n_components_cv+1)]
    pca_cell_via_test = pd.DataFrame(pca_cell_via_test, columns=cols)
    pca_cell_via_test['sig_id'] = test_features['sig_id']

    train_features = train_features.merge(pca_gene_exp, how='inner', on='sig_id')
    train_features = train_features.merge(pca_cell_via, how='inner', on='sig_id')

    test_features = test_features.merge(pca_gene_exp_test, how='inner', on='sig_id')
    test_features = test_features.merge(pca_cell_via_test, how='inner', on='sig_id')
    
    train_features, test_features = engineer_features(train_features,test_features)
    
    ss = StandardScaler()
    ss.fit(train_features[train_features.columns[4:]])

    train_features[train_features.columns[4:]] = ss.transform(train_features[train_features.columns[4:]])

    ss = StandardScaler()
    ss.fit(test_features[test_features.columns[4:]])

    test_features[test_features.columns[4:]] = ss.transform(test_features[test_features.columns[4:]])

    return train_features, train_labels, test_features, test_labels

In [7]:
train_features, train_labels, test_features, test_labels = make_train_test()

C:\Users\leesc\miniconda3\envs\tensorflownew\lib\site-packages\ipykernel_launcher.py:14: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  
C:\Users\leesc\miniconda3\envs\tensorflownew\lib\site-packages\ipykernel_launcher.py:15: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  from ipykernel import kernelapp as app


In [8]:
p_min = 0.0005
p_max = 0.9995
def logloss(y_true, y_pred): #training logloss function
    y_pred = tf.clip_by_value(y_pred,p_min,p_max)
    return -backend.mean(y_true*backend.log(y_pred) + (1-y_true)*backend.log(1-y_pred))

In [9]:
def create_model(hp):
    model = tf.keras.Sequential()
    model.add(tf.keras.layers.BatchNormalization())
    
    model.add(tfa.layers.WeightNormalization(tf.keras.layers.Dense(len(train_features.columns[2:]), activation='relu')))
    model.add(tf.keras.layers.BatchNormalization())
    model.add(tf.keras.layers.Dropout(hp.Float('Dropout_0',.2,.8,.05)))
    
    for i in range(random.choice([3,4,5,6])):
        model.add(tfa.layers.WeightNormalization(tf.keras.layers.Dense(hp.Int(f'{i}_dense_layer',
                                                min_value=1500,
                                                max_value=2048,
                                                step=64),activation='relu')))
        model.add(tf.keras.layers.BatchNormalization())
        model.add(tf.keras.layers.Dropout(hp.Float(f'Dropout_{i+1}',.2,.8,.05)))
        num_dense = i
        
    for j in range(random.choice([1,2,3])):
        model.add(tfa.layers.WeightNormalization(tf.keras.layers.Dense(hp.Int(f'{j+num_dense}_dense_layer',
                                                min_value=128,
                                                max_value=512,
                                                step=64),activation='relu')))
        model.add(tf.keras.layers.BatchNormalization())
        model.add(tf.keras.layers.Dropout(hp.Float(f'Dropout_{i+1}',.2,.8,.05)))

    model.add(tf.keras.layers.Dense(len(train_labels.columns[1:]), activation='sigmoid'))
    
    model.compile(optimizer='adam', loss=tf.keras.losses.BinaryCrossentropy(label_smoothing=0.0005), metrics=logloss)
    
    return model

In [10]:
'''def create_model(hp):
    model = tf.keras.Sequential()
    model.add(tf.keras.layers.BatchNormalization())
    
    model.add(tfa.layers.WeightNormalization(tf.keras.layers.Dense(len(train_features.columns[2:]), activation='relu')))
    model.add(tf.keras.layers.BatchNormalization())
    model.add(tf.keras.layers.Dropout(0.45))
    
    for i in range(3):
        model.add(tfa.layers.WeightNormalization(tf.keras.layers.Dense(hp.Int(f'{i}_dense_layer',
                                                min_value=1000,
                                                max_value=1500,
                                                step=64),activation='relu')))
        model.add(tf.keras.layers.BatchNormalization())
        model.add(tf.keras.layers.Dropout(hp.Float(f'Dropout_{i+1}',.3,.6,.05)))
        num_dense = i
        
    for j in range(2):
        model.add(tfa.layers.WeightNormalization(tf.keras.layers.Dense(hp.Int(f'{j+num_dense}_dense_layer',
                                                min_value=128,
                                                max_value=512,
                                                step=64),activation='relu')))
        model.add(tf.keras.layers.BatchNormalization())
        model.add(tf.keras.layers.Dropout(hp.Float(f'Dropout_{i+1}',.2,.45,.05)))

    model.add(tf.keras.layers.Dense(len(train_labels.columns[1:]), activation='sigmoid'))
    
    model.compile(optimizer='adam', loss=tf.keras.losses.BinaryCrossentropy(label_smoothing=0.0005), metrics=logloss)
    
    return model'''

"def create_model(hp):\n    model = tf.keras.Sequential()\n    model.add(tf.keras.layers.BatchNormalization())\n    \n    model.add(tfa.layers.WeightNormalization(tf.keras.layers.Dense(len(train_features.columns[2:]), activation='relu')))\n    model.add(tf.keras.layers.BatchNormalization())\n    model.add(tf.keras.layers.Dropout(0.45))\n    \n    for i in range(3):\n        model.add(tfa.layers.WeightNormalization(tf.keras.layers.Dense(hp.Int(f'{i}_dense_layer',\n                                                min_value=1000,\n                                                max_value=1500,\n                                                step=64),activation='relu')))\n        model.add(tf.keras.layers.BatchNormalization())\n        model.add(tf.keras.layers.Dropout(hp.Float(f'Dropout_{i+1}',.3,.6,.05)))\n        num_dense = i\n        \n    for j in range(2):\n        model.add(tfa.layers.WeightNormalization(tf.keras.layers.Dense(hp.Int(f'{j+num_dense}_dense_layer',\n                  

In [11]:
tuner = RandomSearch(
    create_model,
    objective=kerastuner.Objective("val_logloss", direction="min"),
    max_trials=10,  # how many model variations to test?
    executions_per_trial=1,  # how many trials per variation? (same model could perform differently)
    directory=directory,
    project_name='NN')

In [12]:
early_stop = EarlyStopping(monitor='val_logloss', patience=10,verbose=0)
reduce_lr = ReduceLROnPlateau(monitor='val_logloss', factor=0.3, patience=5, mode='min', min_lr=1e-5)
callbacks_list = [early_stop, reduce_lr]

tuner.search(x=train_features.drop(['sig_id','cp_type'],axis=1),
             y=train_labels.drop(['sig_id'],axis=1),
             verbose=1,
             epochs=10000, #this will break with Early Stopping
             batch_size=256,
             callbacks=callbacks_list,
             validation_split=0.1
            )

Epoch 1/10000
70/70 [==============================] - ETA: 7s - loss: 0.7866 - logloss: 0.786 - ETA: 8s - loss: 0.7824 - logloss: 0.782 - ETA: 8s - loss: 0.7784 - logloss: 0.778 - ETA: 8s - loss: 0.7740 - logloss: 0.773 - ETA: 8s - loss: 0.7695 - logloss: 0.769 - ETA: 8s - loss: 0.7657 - logloss: 0.765 - ETA: 8s - loss: 0.7618 - logloss: 0.761 - ETA: 8s - loss: 0.7582 - logloss: 0.758 - ETA: 8s - loss: 0.7548 - logloss: 0.754 - ETA: 8s - loss: 0.7517 - logloss: 0.751 - ETA: 8s - loss: 0.7487 - logloss: 0.748 - ETA: 8s - loss: 0.7460 - logloss: 0.745 - ETA: 8s - loss: 0.7436 - logloss: 0.743 - ETA: 8s - loss: 0.7413 - logloss: 0.741 - ETA: 7s - loss: 0.7391 - logloss: 0.738 - ETA: 7s - loss: 0.7370 - logloss: 0.736 - ETA: 7s - loss: 0.7351 - logloss: 0.734 - ETA: 7s - loss: 0.7333 - logloss: 0.733 - ETA: 7s - loss: 0.7315 - logloss: 0.731 - ETA: 7s - loss: 0.7299 - logloss: 0.729 - ETA: 7s - loss: 0.7283 - logloss: 0.728 - ETA: 6s - loss: 0.7269 - logloss: 0.726 - ETA: 6s - loss: 0.725

70/70 [==============================] - ETA: 0s - loss: 0.1311 - logloss: 0.130 - ETA: 5s - loss: 0.1314 - logloss: 0.130 - ETA: 6s - loss: 0.1297 - logloss: 0.128 - ETA: 7s - loss: 0.1290 - logloss: 0.128 - ETA: 8s - loss: 0.1326 - logloss: 0.130 - ETA: 8s - loss: 0.1318 - logloss: 0.130 - ETA: 8s - loss: 0.1299 - logloss: 0.128 - ETA: 8s - loss: 0.1279 - logloss: 0.126 - ETA: 8s - loss: 0.1279 - logloss: 0.126 - ETA: 8s - loss: 0.1262 - logloss: 0.124 - ETA: 8s - loss: 0.1251 - logloss: 0.123 - ETA: 8s - loss: 0.1238 - logloss: 0.122 - ETA: 8s - loss: 0.1229 - logloss: 0.121 - ETA: 8s - loss: 0.1230 - logloss: 0.121 - ETA: 8s - loss: 0.1215 - logloss: 0.120 - ETA: 7s - loss: 0.1201 - logloss: 0.118 - ETA: 7s - loss: 0.1187 - logloss: 0.117 - ETA: 7s - loss: 0.1177 - logloss: 0.116 - ETA: 7s - loss: 0.1168 - logloss: 0.115 - ETA: 7s - loss: 0.1165 - logloss: 0.115 - ETA: 7s - loss: 0.1155 - logloss: 0.114 - ETA: 7s - loss: 0.1144 - logloss: 0.113 - ETA: 7s - loss: 0.1134 - logloss: 0

70/70 [==============================] - ETA: 0s - loss: 0.0343 - logloss: 0.033 - ETA: 5s - loss: 0.0335 - logloss: 0.032 - ETA: 6s - loss: 0.0333 - logloss: 0.032 - ETA: 7s - loss: 0.0333 - logloss: 0.032 - ETA: 8s - loss: 0.0332 - logloss: 0.032 - ETA: 8s - loss: 0.0333 - logloss: 0.032 - ETA: 8s - loss: 0.0333 - logloss: 0.032 - ETA: 8s - loss: 0.0332 - logloss: 0.032 - ETA: 8s - loss: 0.0332 - logloss: 0.032 - ETA: 8s - loss: 0.0330 - logloss: 0.031 - ETA: 8s - loss: 0.0330 - logloss: 0.031 - ETA: 8s - loss: 0.0330 - logloss: 0.031 - ETA: 8s - loss: 0.0329 - logloss: 0.031 - ETA: 8s - loss: 0.0329 - logloss: 0.031 - ETA: 8s - loss: 0.0329 - logloss: 0.031 - ETA: 7s - loss: 0.0328 - logloss: 0.031 - ETA: 7s - loss: 0.0327 - logloss: 0.031 - ETA: 7s - loss: 0.0327 - logloss: 0.031 - ETA: 7s - loss: 0.0327 - logloss: 0.031 - ETA: 7s - loss: 0.0327 - logloss: 0.031 - ETA: 7s - loss: 0.0325 - logloss: 0.031 - ETA: 7s - loss: 0.0324 - logloss: 0.031 - ETA: 7s - loss: 0.0324 - logloss: 0

70/70 [==============================] - ETA: 0s - loss: 0.0250 - logloss: 0.023 - ETA: 5s - loss: 0.0264 - logloss: 0.024 - ETA: 6s - loss: 0.0261 - logloss: 0.024 - ETA: 7s - loss: 0.0260 - logloss: 0.024 - ETA: 8s - loss: 0.0260 - logloss: 0.024 - ETA: 8s - loss: 0.0258 - logloss: 0.024 - ETA: 8s - loss: 0.0256 - logloss: 0.024 - ETA: 8s - loss: 0.0258 - logloss: 0.024 - ETA: 8s - loss: 0.0257 - logloss: 0.024 - ETA: 8s - loss: 0.0256 - logloss: 0.024 - ETA: 8s - loss: 0.0257 - logloss: 0.024 - ETA: 8s - loss: 0.0256 - logloss: 0.024 - ETA: 8s - loss: 0.0255 - logloss: 0.024 - ETA: 8s - loss: 0.0256 - logloss: 0.024 - ETA: 8s - loss: 0.0255 - logloss: 0.024 - ETA: 8s - loss: 0.0257 - logloss: 0.024 - ETA: 7s - loss: 0.0256 - logloss: 0.024 - ETA: 7s - loss: 0.0256 - logloss: 0.024 - ETA: 7s - loss: 0.0256 - logloss: 0.024 - ETA: 7s - loss: 0.0257 - logloss: 0.024 - ETA: 7s - loss: 0.0257 - logloss: 0.024 - ETA: 7s - loss: 0.0256 - logloss: 0.024 - ETA: 7s - loss: 0.0256 - logloss: 0

70/70 [==============================] - ETA: 0s - loss: 0.0216 - logloss: 0.020 - ETA: 5s - loss: 0.0228 - logloss: 0.021 - ETA: 7s - loss: 0.0229 - logloss: 0.021 - ETA: 7s - loss: 0.0232 - logloss: 0.021 - ETA: 8s - loss: 0.0232 - logloss: 0.021 - ETA: 8s - loss: 0.0236 - logloss: 0.022 - ETA: 8s - loss: 0.0236 - logloss: 0.022 - ETA: 8s - loss: 0.0236 - logloss: 0.022 - ETA: 8s - loss: 0.0235 - logloss: 0.022 - ETA: 8s - loss: 0.0237 - logloss: 0.022 - ETA: 8s - loss: 0.0235 - logloss: 0.022 - ETA: 8s - loss: 0.0235 - logloss: 0.022 - ETA: 8s - loss: 0.0235 - logloss: 0.022 - ETA: 8s - loss: 0.0235 - logloss: 0.022 - ETA: 8s - loss: 0.0236 - logloss: 0.022 - ETA: 8s - loss: 0.0236 - logloss: 0.022 - ETA: 7s - loss: 0.0236 - logloss: 0.022 - ETA: 7s - loss: 0.0236 - logloss: 0.022 - ETA: 7s - loss: 0.0237 - logloss: 0.022 - ETA: 7s - loss: 0.0237 - logloss: 0.022 - ETA: 7s - loss: 0.0239 - logloss: 0.022 - ETA: 7s - loss: 0.0239 - logloss: 0.022 - ETA: 7s - loss: 0.0238 - logloss: 0

...

70/70 [==============================] - ETA: 0s - loss: 0.0176 - logloss: 0.015 - ETA: 6s - loss: 0.0180 - logloss: 0.016 - ETA: 9s - loss: 0.0182 - logloss: 0.016 - ETA: 10s - loss: 0.0184 - logloss: 0.01 - ETA: 10s - loss: 0.0186 - logloss: 0.01 - ETA: 10s - loss: 0.0189 - logloss: 0.01 - ETA: 11s - loss: 0.0188 - logloss: 0.01 - ETA: 11s - loss: 0.0188 - logloss: 0.01 - ETA: 11s - loss: 0.0187 - logloss: 0.01 - ETA: 11s - loss: 0.0186 - logloss: 0.01 - ETA: 11s - loss: 0.0186 - logloss: 0.01 - ETA: 10s - loss: 0.0187 - logloss: 0.01 - ETA: 10s - loss: 0.0185 - logloss: 0.01 - ETA: 10s - loss: 0.0185 - logloss: 0.01 - ETA: 10s - loss: 0.0185 - logloss: 0.01 - ETA: 10s - loss: 0.0184 - logloss: 0.01 - ETA: 10s - loss: 0.0184 - logloss: 0.01 - ETA: 10s - loss: 0.0184 - logloss: 0.01 - ETA: 9s - loss: 0.0184 - logloss: 0.0167 - ETA: 9s - loss: 0.0185 - logloss: 0.016 - ETA: 9s - loss: 0.0185 - logloss: 0.016 - ETA: 9s - loss: 0.0185 - logloss: 0.016 - ETA: 9s - loss: 0.0185 - logloss: 

70/70 [==============================] - ETA: 0s - loss: 0.0201 - logloss: 0.018 - ETA: 7s - loss: 0.0184 - logloss: 0.016 - ETA: 9s - loss: 0.0182 - logloss: 0.016 - ETA: 10s - loss: 0.0181 - logloss: 0.01 - ETA: 10s - loss: 0.0180 - logloss: 0.01 - ETA: 11s - loss: 0.0181 - logloss: 0.01 - ETA: 11s - loss: 0.0180 - logloss: 0.01 - ETA: 11s - loss: 0.0182 - logloss: 0.01 - ETA: 11s - loss: 0.0182 - logloss: 0.01 - ETA: 11s - loss: 0.0181 - logloss: 0.01 - ETA: 11s - loss: 0.0182 - logloss: 0.01 - ETA: 10s - loss: 0.0182 - logloss: 0.01 - ETA: 10s - loss: 0.0182 - logloss: 0.01 - ETA: 10s - loss: 0.0183 - logloss: 0.01 - ETA: 10s - loss: 0.0182 - logloss: 0.01 - ETA: 10s - loss: 0.0181 - logloss: 0.01 - ETA: 10s - loss: 0.0181 - logloss: 0.01 - ETA: 10s - loss: 0.0182 - logloss: 0.01 - ETA: 9s - loss: 0.0182 - logloss: 0.0164 - ETA: 9s - loss: 0.0181 - logloss: 0.016 - ETA: 9s - loss: 0.0181 - logloss: 0.016 - ETA: 9s - loss: 0.0181 - logloss: 0.016 - ETA: 9s - loss: 0.0182 - logloss: 

70/70 [==============================] - ETA: 0s - loss: 0.0188 - logloss: 0.017 - ETA: 6s - loss: 0.0191 - logloss: 0.017 - ETA: 9s - loss: 0.0185 - logloss: 0.016 - ETA: 10s - loss: 0.0187 - logloss: 0.01 - ETA: 10s - loss: 0.0186 - logloss: 0.01 - ETA: 10s - loss: 0.0188 - logloss: 0.01 - ETA: 10s - loss: 0.0188 - logloss: 0.01 - ETA: 10s - loss: 0.0189 - logloss: 0.01 - ETA: 10s - loss: 0.0190 - logloss: 0.01 - ETA: 10s - loss: 0.0189 - logloss: 0.01 - ETA: 10s - loss: 0.0186 - logloss: 0.01 - ETA: 10s - loss: 0.0186 - logloss: 0.01 - ETA: 10s - loss: 0.0186 - logloss: 0.01 - ETA: 10s - loss: 0.0186 - logloss: 0.01 - ETA: 10s - loss: 0.0185 - logloss: 0.01 - ETA: 10s - loss: 0.0184 - logloss: 0.01 - ETA: 9s - loss: 0.0185 - logloss: 0.0167 - ETA: 9s - loss: 0.0185 - logloss: 0.016 - ETA: 9s - loss: 0.0184 - logloss: 0.016 - ETA: 9s - loss: 0.0184 - logloss: 0.016 - ETA: 9s - loss: 0.0183 - logloss: 0.016 - ETA: 9s - loss: 0.0183 - logloss: 0.016 - ETA: 8s - loss: 0.0183 - logloss: 

70/70 [==============================] - ETA: 0s - loss: 0.0172 - logloss: 0.015 - ETA: 7s - loss: 0.0171 - logloss: 0.015 - ETA: 9s - loss: 0.0178 - logloss: 0.016 - ETA: 10s - loss: 0.0178 - logloss: 0.01 - ETA: 10s - loss: 0.0177 - logloss: 0.01 - ETA: 10s - loss: 0.0178 - logloss: 0.01 - ETA: 10s - loss: 0.0181 - logloss: 0.01 - ETA: 10s - loss: 0.0182 - logloss: 0.01 - ETA: 10s - loss: 0.0182 - logloss: 0.01 - ETA: 10s - loss: 0.0184 - logloss: 0.01 - ETA: 10s - loss: 0.0184 - logloss: 0.01 - ETA: 10s - loss: 0.0184 - logloss: 0.01 - ETA: 10s - loss: 0.0184 - logloss: 0.01 - ETA: 10s - loss: 0.0184 - logloss: 0.01 - ETA: 10s - loss: 0.0184 - logloss: 0.01 - ETA: 10s - loss: 0.0184 - logloss: 0.01 - ETA: 9s - loss: 0.0183 - logloss: 0.0165 - ETA: 9s - loss: 0.0184 - logloss: 0.016 - ETA: 9s - loss: 0.0183 - logloss: 0.016 - ETA: 9s - loss: 0.0183 - logloss: 0.016 - ETA: 9s - loss: 0.0183 - logloss: 0.016 - ETA: 9s - loss: 0.0184 - logloss: 0.016 - ETA: 8s - loss: 0.0184 - logloss: 

INFO:tensorflow:Oracle triggered exit


In [13]:
from logloss import log_loss #log_loss = actual logloss function, logloss = logloss for NN

#test model on many splits
model_summ = {}
get_top_n = 3
n_splits = 3
for n_model in range(get_top_n):
    model_scores = []
    for split in range(n_splits):
        train_features, train_labels, test_features, test_labels = make_train_test()
        best_model = create_model(tuner.get_best_hyperparameters(num_trials=get_top_n)[n_model])
        print(f'fitting model {n_model+1}/{get_top_n} split {split+1}/{n_splits}...')
        best_model.fit( x=train_features.drop(['sig_id','cp_type'],axis=1),
                   y=train_labels.drop(['sig_id'],axis=1),
                   batch_size=256,
                   epochs=10000,
                   validation_split=0.1,
                   verbose=0,
                   callbacks=callbacks_list )

        samp_sub = pd.read_csv('sample_submission.csv')
        samp_sub = samp_sub[:len(test_features)]

        #for scoring on fake test set
        preds = []
        true = []
        print('predicting...')
        for i in tqdm(range(len(test_features))):
            sample = np.array(test_features.drop(['sig_id','cp_type'],axis=1).iloc[i]).reshape(1,len(test_features.drop(['sig_id','cp_type'],axis=1).columns))
            preds.append(best_model.predict(sample)[0])
            true.append(test_labels.drop(['sig_id'],axis=1).iloc[i])

        samp_sub[samp_sub.columns[1:]] = preds
        samp_sub['sig_id'] = test_features['sig_id']
        
        print('scoring...')
        scores = []
        for j in range(len(preds)):
            scores.append(log_loss(true[j],preds[j]))
        print(f'Log loss model {n_model} split {split+1}: {np.mean(scores)}')
        model_scores.append(np.mean(scores))
    model_summ[n_model] = np.mean(model_scores)


C:\Users\leesc\miniconda3\envs\tensorflownew\lib\site-packages\ipykernel_launcher.py:14: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  
C:\Users\leesc\miniconda3\envs\tensorflownew\lib\site-packages\ipykernel_launcher.py:15: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  from ipykernel import kernelapp as app


fitting model 1/3 split 1/3...
predicting...


100%|██████████████████████████████████████████████████████████████████████████████| 2195/2195 [01:40<00:00, 21.84it/s]


scoring...
Log loss model 0 split 1: 0.01700664962308062


C:\Users\leesc\miniconda3\envs\tensorflownew\lib\site-packages\ipykernel_launcher.py:14: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  
C:\Users\leesc\miniconda3\envs\tensorflownew\lib\site-packages\ipykernel_launcher.py:15: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  from ipykernel import kernelapp as app


...

100%|██████████████████████████████████████████████████████████████████████████████| 2195/2195 [01:38<00:00, 22.25it/s]


scoring...
Log loss model 0 split 3: 0.016257894164757463


C:\Users\leesc\miniconda3\envs\tensorflownew\lib\site-packages\ipykernel_launcher.py:14: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  
C:\Users\leesc\miniconda3\envs\tensorflownew\lib\site-packages\ipykernel_launcher.py:15: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  from ipykernel import kernelapp as app


fitting model 2/3 split 1/3...


KeyboardInterrupt: 

In [14]:
model_summ

{0: 0.016871666393158725}

In [16]:
best_model = create_model(tuner.get_best_hyperparameters(num_trials=get_top_n)[min(model_summ, key=model_summ.get)])
train_features, train_labels, test_features, test_labels = make_train_test()
best_model.fit( x=train_features.drop(['sig_id','cp_type'],axis=1),
                   y=train_labels.drop(['sig_id'],axis=1),
                   batch_size=256,
                   epochs=10000,
                   validation_split=0.1,
                   verbose=1,
                   callbacks=callbacks_list )

best_model.save(f'C:\\Users\\leesc\\Documents\\MoA_comp_drafting\\logs\\{model_summ[min(model_summ, key=model_summ.get)]}.h5')

C:\Users\leesc\miniconda3\envs\tensorflownew\lib\site-packages\ipykernel_launcher.py:14: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  
C:\Users\leesc\miniconda3\envs\tensorflownew\lib\site-packages\ipykernel_launcher.py:15: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  from ipykernel import kernelapp as app


Epoch 1/10000
70/70 [==============================] - ETA: 8s - loss: 0.8863 - logloss: 0.885 - ETA: 9s - loss: 0.8793 - logloss: 0.878 - ETA: 10s - loss: 0.8706 - logloss: 0.86 - ETA: 10s - loss: 0.8607 - logloss: 0.85 - ETA: 10s - loss: 0.8519 - logloss: 0.85 - ETA: 10s - loss: 0.8438 - logloss: 0.84 - ETA: 10s - loss: 0.8363 - logloss: 0.83 - ETA: 10s - loss: 0.8291 - logloss: 0.82 - ETA: 10s - loss: 0.8227 - logloss: 0.82 - ETA: 10s - loss: 0.8160 - logloss: 0.81 - ETA: 10s - loss: 0.8102 - logloss: 0.80 - ETA: 10s - loss: 0.8049 - logloss: 0.80 - ETA: 9s - loss: 0.8004 - logloss: 0.7977 - ETA: 9s - loss: 0.7957 - logloss: 0.792 - ETA: 9s - loss: 0.7919 - logloss: 0.789 - ETA: 9s - loss: 0.7885 - logloss: 0.785 - ETA: 9s - loss: 0.7848 - logloss: 0.782 - ETA: 9s - loss: 0.7812 - logloss: 0.778 - ETA: 8s - loss: 0.7777 - logloss: 0.774 - ETA: 8s - loss: 0.7747 - logloss: 0.771 - ETA: 8s - loss: 0.7717 - logloss: 0.768 - ETA: 8s - loss: 0.7690 - logloss: 0.766 - ETA: 8s - loss: 0.76

70/70 [==============================] - ETA: 0s - loss: 0.0504 - logloss: 0.049 - ETA: 6s - loss: 0.0547 - logloss: 0.052 - ETA: 8s - loss: 0.0529 - logloss: 0.051 - ETA: 9s - loss: 0.0516 - logloss: 0.050 - ETA: 10s - loss: 0.0512 - logloss: 0.04 - ETA: 10s - loss: 0.0503 - logloss: 0.04 - ETA: 10s - loss: 0.0501 - logloss: 0.04 - ETA: 10s - loss: 0.0498 - logloss: 0.04 - ETA: 10s - loss: 0.0493 - logloss: 0.04 - ETA: 10s - loss: 0.0489 - logloss: 0.04 - ETA: 10s - loss: 0.0490 - logloss: 0.04 - ETA: 10s - loss: 0.0490 - logloss: 0.04 - ETA: 10s - loss: 0.0487 - logloss: 0.04 - ETA: 10s - loss: 0.0484 - logloss: 0.04 - ETA: 9s - loss: 0.0483 - logloss: 0.0469 - ETA: 9s - loss: 0.0482 - logloss: 0.046 - ETA: 9s - loss: 0.0478 - logloss: 0.046 - ETA: 9s - loss: 0.0474 - logloss: 0.046 - ETA: 9s - loss: 0.0471 - logloss: 0.045 - ETA: 9s - loss: 0.0468 - logloss: 0.045 - ETA: 9s - loss: 0.0465 - logloss: 0.045 - ETA: 8s - loss: 0.0462 - logloss: 0.044 - ETA: 8s - loss: 0.0458 - logloss: 

70/70 [==============================] - ETA: 0s - loss: 0.0260 - logloss: 0.024 - ETA: 6s - loss: 0.0260 - logloss: 0.024 - ETA: 8s - loss: 0.0257 - logloss: 0.024 - ETA: 9s - loss: 0.0258 - logloss: 0.024 - ETA: 10s - loss: 0.0259 - logloss: 0.02 - ETA: 10s - loss: 0.0256 - logloss: 0.02 - ETA: 10s - loss: 0.0256 - logloss: 0.02 - ETA: 10s - loss: 0.0255 - logloss: 0.02 - ETA: 10s - loss: 0.0256 - logloss: 0.02 - ETA: 10s - loss: 0.0256 - logloss: 0.02 - ETA: 10s - loss: 0.0257 - logloss: 0.02 - ETA: 10s - loss: 0.0257 - logloss: 0.02 - ETA: 10s - loss: 0.0257 - logloss: 0.02 - ETA: 10s - loss: 0.0255 - logloss: 0.02 - ETA: 9s - loss: 0.0255 - logloss: 0.0240 - ETA: 9s - loss: 0.0254 - logloss: 0.023 - ETA: 9s - loss: 0.0254 - logloss: 0.023 - ETA: 9s - loss: 0.0255 - logloss: 0.024 - ETA: 9s - loss: 0.0254 - logloss: 0.023 - ETA: 9s - loss: 0.0255 - logloss: 0.024 - ETA: 9s - loss: 0.0255 - logloss: 0.024 - ETA: 8s - loss: 0.0255 - logloss: 0.024 - ETA: 8s - loss: 0.0255 - logloss: 

70/70 [==============================] - ETA: 0s - loss: 0.0246 - logloss: 0.023 - ETA: 6s - loss: 0.0237 - logloss: 0.022 - ETA: 8s - loss: 0.0237 - logloss: 0.022 - ETA: 9s - loss: 0.0233 - logloss: 0.021 - ETA: 10s - loss: 0.0232 - logloss: 0.02 - ETA: 10s - loss: 0.0232 - logloss: 0.02 - ETA: 10s - loss: 0.0233 - logloss: 0.02 - ETA: 10s - loss: 0.0235 - logloss: 0.02 - ETA: 10s - loss: 0.0234 - logloss: 0.02 - ETA: 10s - loss: 0.0234 - logloss: 0.02 - ETA: 10s - loss: 0.0233 - logloss: 0.02 - ETA: 10s - loss: 0.0234 - logloss: 0.02 - ETA: 10s - loss: 0.0234 - logloss: 0.02 - ETA: 10s - loss: 0.0233 - logloss: 0.02 - ETA: 9s - loss: 0.0234 - logloss: 0.0219 - ETA: 9s - loss: 0.0233 - logloss: 0.021 - ETA: 9s - loss: 0.0233 - logloss: 0.021 - ETA: 9s - loss: 0.0234 - logloss: 0.021 - ETA: 9s - loss: 0.0234 - logloss: 0.021 - ETA: 9s - loss: 0.0234 - logloss: 0.021 - ETA: 9s - loss: 0.0234 - logloss: 0.021 - ETA: 8s - loss: 0.0234 - logloss: 0.022 - ETA: 8s - loss: 0.0234 - logloss: 

...

70/70 [==============================] - ETA: 0s - loss: 0.0171 - logloss: 0.015 - ETA: 6s - loss: 0.0175 - logloss: 0.015 - ETA: 8s - loss: 0.0177 - logloss: 0.016 - ETA: 9s - loss: 0.0178 - logloss: 0.016 - ETA: 10s - loss: 0.0180 - logloss: 0.01 - ETA: 10s - loss: 0.0183 - logloss: 0.01 - ETA: 10s - loss: 0.0182 - logloss: 0.01 - ETA: 10s - loss: 0.0184 - logloss: 0.01 - ETA: 10s - loss: 0.0184 - logloss: 0.01 - ETA: 10s - loss: 0.0185 - logloss: 0.01 - ETA: 10s - loss: 0.0185 - logloss: 0.01 - ETA: 10s - loss: 0.0185 - logloss: 0.01 - ETA: 10s - loss: 0.0185 - logloss: 0.01 - ETA: 10s - loss: 0.0185 - logloss: 0.01 - ETA: 9s - loss: 0.0186 - logloss: 0.0169 - ETA: 9s - loss: 0.0186 - logloss: 0.016 - ETA: 9s - loss: 0.0186 - logloss: 0.016 - ETA: 9s - loss: 0.0186 - logloss: 0.016 - ETA: 9s - loss: 0.0185 - logloss: 0.016 - ETA: 9s - loss: 0.0184 - logloss: 0.016 - ETA: 9s - loss: 0.0184 - logloss: 0.016 - ETA: 8s - loss: 0.0184 - logloss: 0.016 - ETA: 8s - loss: 0.0183 - logloss: 

70/70 [==============================] - ETA: 0s - loss: 0.0181 - logloss: 0.016 - ETA: 6s - loss: 0.0179 - logloss: 0.016 - ETA: 8s - loss: 0.0179 - logloss: 0.016 - ETA: 9s - loss: 0.0177 - logloss: 0.016 - ETA: 10s - loss: 0.0180 - logloss: 0.01 - ETA: 10s - loss: 0.0179 - logloss: 0.01 - ETA: 10s - loss: 0.0181 - logloss: 0.01 - ETA: 10s - loss: 0.0181 - logloss: 0.01 - ETA: 10s - loss: 0.0182 - logloss: 0.01 - ETA: 10s - loss: 0.0183 - logloss: 0.01 - ETA: 10s - loss: 0.0183 - logloss: 0.01 - ETA: 10s - loss: 0.0183 - logloss: 0.01 - ETA: 10s - loss: 0.0183 - logloss: 0.01 - ETA: 10s - loss: 0.0181 - logloss: 0.01 - ETA: 9s - loss: 0.0182 - logloss: 0.0165 - ETA: 9s - loss: 0.0182 - logloss: 0.016 - ETA: 9s - loss: 0.0182 - logloss: 0.016 - ETA: 9s - loss: 0.0182 - logloss: 0.016 - ETA: 9s - loss: 0.0181 - logloss: 0.016 - ETA: 9s - loss: 0.0181 - logloss: 0.016 - ETA: 9s - loss: 0.0181 - logloss: 0.016 - ETA: 8s - loss: 0.0181 - logloss: 0.016 - ETA: 8s - loss: 0.0181 - logloss: 

70/70 [==============================] - ETA: 0s - loss: 0.0185 - logloss: 0.016 - ETA: 6s - loss: 0.0179 - logloss: 0.016 - ETA: 8s - loss: 0.0175 - logloss: 0.015 - ETA: 9s - loss: 0.0180 - logloss: 0.016 - ETA: 10s - loss: 0.0185 - logloss: 0.01 - ETA: 10s - loss: 0.0186 - logloss: 0.01 - ETA: 10s - loss: 0.0184 - logloss: 0.01 - ETA: 10s - loss: 0.0185 - logloss: 0.01 - ETA: 10s - loss: 0.0186 - logloss: 0.01 - ETA: 10s - loss: 0.0185 - logloss: 0.01 - ETA: 10s - loss: 0.0187 - logloss: 0.01 - ETA: 10s - loss: 0.0188 - logloss: 0.01 - ETA: 10s - loss: 0.0186 - logloss: 0.01 - ETA: 10s - loss: 0.0186 - logloss: 0.01 - ETA: 9s - loss: 0.0185 - logloss: 0.0168 - ETA: 9s - loss: 0.0186 - logloss: 0.016 - ETA: 9s - loss: 0.0185 - logloss: 0.016 - ETA: 9s - loss: 0.0185 - logloss: 0.016 - ETA: 9s - loss: 0.0185 - logloss: 0.016 - ETA: 9s - loss: 0.0185 - logloss: 0.016 - ETA: 9s - loss: 0.0184 - logloss: 0.016 - ETA: 8s - loss: 0.0184 - logloss: 0.016 - ETA: 8s - loss: 0.0184 - logloss: 

70/70 [==============================] - ETA: 0s - loss: 0.0181 - logloss: 0.016 - ETA: 6s - loss: 0.0174 - logloss: 0.015 - ETA: 8s - loss: 0.0176 - logloss: 0.015 - ETA: 9s - loss: 0.0177 - logloss: 0.016 - ETA: 10s - loss: 0.0177 - logloss: 0.01 - ETA: 10s - loss: 0.0181 - logloss: 0.01 - ETA: 10s - loss: 0.0182 - logloss: 0.01 - ETA: 10s - loss: 0.0181 - logloss: 0.01 - ETA: 10s - loss: 0.0182 - logloss: 0.01 - ETA: 10s - loss: 0.0183 - logloss: 0.01 - ETA: 10s - loss: 0.0182 - logloss: 0.01 - ETA: 10s - loss: 0.0182 - logloss: 0.01 - ETA: 10s - loss: 0.0184 - logloss: 0.01 - ETA: 10s - loss: 0.0185 - logloss: 0.01 - ETA: 10s - loss: 0.0185 - logloss: 0.01 - ETA: 9s - loss: 0.0184 - logloss: 0.0167 - ETA: 9s - loss: 0.0183 - logloss: 0.016 - ETA: 9s - loss: 0.0183 - logloss: 0.016 - ETA: 9s - loss: 0.0183 - logloss: 0.016 - ETA: 9s - loss: 0.0184 - logloss: 0.016 - ETA: 9s - loss: 0.0184 - logloss: 0.016 - ETA: 8s - loss: 0.0184 - logloss: 0.016 - ETA: 8s - loss: 0.0184 - logloss: 

70/70 [==============================] - ETA: 0s - loss: 0.0177 - logloss: 0.016 - ETA: 6s - loss: 0.0177 - logloss: 0.016 - ETA: 8s - loss: 0.0175 - logloss: 0.015 - ETA: 9s - loss: 0.0178 - logloss: 0.016 - ETA: 10s - loss: 0.0180 - logloss: 0.01 - ETA: 10s - loss: 0.0178 - logloss: 0.01 - ETA: 10s - loss: 0.0179 - logloss: 0.01 - ETA: 10s - loss: 0.0178 - logloss: 0.01 - ETA: 10s - loss: 0.0180 - logloss: 0.01 - ETA: 10s - loss: 0.0179 - logloss: 0.01 - ETA: 10s - loss: 0.0180 - logloss: 0.01 - ETA: 10s - loss: 0.0180 - logloss: 0.01 - ETA: 10s - loss: 0.0180 - logloss: 0.01 - ETA: 10s - loss: 0.0180 - logloss: 0.01 - ETA: 10s - loss: 0.0180 - logloss: 0.01 - ETA: 9s - loss: 0.0180 - logloss: 0.0163 - ETA: 9s - loss: 0.0180 - logloss: 0.016 - ETA: 9s - loss: 0.0181 - logloss: 0.016 - ETA: 9s - loss: 0.0181 - logloss: 0.016 - ETA: 9s - loss: 0.0180 - logloss: 0.016 - ETA: 9s - loss: 0.0180 - logloss: 0.016 - ETA: 8s - loss: 0.0180 - logloss: 0.016 - ETA: 8s - loss: 0.0180 - logloss: 

In [ ]:
model_summ[min(model_summ, key=model_summ.get)]

In [ ]:
model = tf.keras.models.load_model('C:\\Users\\leesc\\Documents\\MoA_comp_drafting\\logs\\0.017148087104835855.h5',custom_objects={"logloss": logloss})

In [ ]:
model.summary()

In [ ]:
tuner.get_best_hyperparameters(num_trials=get_top_n)[min(model_summ, key=model_summ.get)].values

In [ ]:
tuner.get_best_hyperparameters(num_trials=get_top_n)[min(model_summ, key=model_summ.get)].values

In [ ]:
tuner.get_best_hyperparameters(num_trials=10)[9].values